# Prepare Leaf compoundness data from TRY for use

Leaf compoundness data from TRY informs on whether plant leaves are simple, compound, pinnate, palmate, needle or scale. These categories are not mutually exclusive: pinnate and palmate leaves are also compound leaves. The script takes this into account.

*If you intend to clean more than one or two traits, we recommend the use of the batch pre-processing script. Refer to the [TRY main page](try-label) for details.*

If you have questions, suggestions, spot errors, or want to contribute, get in touch with us through planthub@idiv.de.

Author: David Schellenberger Costa

## Requirements

To run the script, the following is needed:
- TRY data, available <a href="https://planthub.idiv.de/downloads/" target="_parent">here</a>
- the data.table library may need to be installed

## Code

In [ ]:
# load in libraries
library(data.table) # handle large datasets

# clear workspace
rm(list = ls())


Let's get the TRY data

In [ ]:
# set working directory (adapt this!)
setwd(paste0(.brd, "PlantHub"))

# read in data (adapt this!)
TRY <- fread("TRY_PlantHub.gz")

# select data of interest
TRYSubset <- TRY[TraitName == "Leaf compoundness"]


To get an overview of the data, we convert values to lowercase, sort them, and show them as
a table.

In [ ]:
# extract original data strings
oriVals <- TRYSubset$OrigValueStr # oriVals == original values

# change all to lowercase to ease later classification
oriVals <- tolower(oriVals)

# get an overview over the data by summarizing values and showing them in alphabetical order
valueOverview <- table(oriVals)
valueOverview[order(valueOverview)]


Apparently, there are some trait categories mixed here. We will prepare a matrix with two columns
to separately save entries describing leaf compoundness and leaf shape (e.g. needle).

In [ ]:
newVals <- matrix(NA, length(oriVals), 2)


The most important part of the cleaning process is the definition of the search strings to look for.
We use regular expressions in some cases to be more inclusive (or exclusive).

In [ ]:
# create a vector containing the search strings to look for
searchNames <- c(
	# leaf compoundness
	"simple|^s$|^no?$|^0$|single|singola|1-foliate",
	"compound|^c$|composite|^y(es)?$|^1$|composte|composta|compuestas",
	"pinnate",
	"palm(ate)?|trifoli(ol)?ate",
	# leaf shape
	"needle",
	"scale",
	"absent"
)


We can now search for the strings defined before and give names to the new categories. We do this for each trait the categories will belong to.

In [ ]:
# search for the strings defined before
searchResults <- sapply(searchNames, grepl, oriVals)

# name columns of searchResults matrix like corrected searchNames
searchResultsCols <- list()
searchResultsCols[[1]] <- c("simple", "compound", "pinnate", "palmate")
searchResultsCols[[2]] <- c("needle", "scale", "aphyllous")
colnames(searchResults) <- unlist(searchResultsCols)


Let's have a look at the results.

In [ ]:
# show the number of matches to each category
colSums(searchResults)

# show the original entries for which no match was retrieved
oriVals[rowSums(searchResults) < 1]

# show the number of entries that weren't matched to any category
sum(rowSums(searchResults) < 1)

# show the number of entries that were matched to more that one category
sum(rowSums(searchResults) > 1)


As these categories should partly be exclusive, we exclude all ambiguous data
by setting our search results to FALSE whenever we found more than
one match in our search. However, some categories are sub-categories of others, and this
also needs to be taken into account (e.g. pinnate leaves are also compound).

In [ ]:
# remove contradictory entries
# only one category possible
searchResults[
	rowSums(searchResults[, colnames(searchResults) %in% searchResultsCols[[2]]]) > 1,
	colnames(searchResults) %in% searchResultsCols[[2]]
] <- FALSE

searchResults[
	rowSums(searchResults[, grep("simple|compound", colnames(searchResults))]) > 1,
	grep("simple|compound", colnames(searchResults))
] <- FALSE
searchResults[
	rowSums(searchResults[, grep("pinnate|palmate", colnames(searchResults))]) > 1,
	grep("pinnate|palmate", colnames(searchResults))
] <- FALSE
searchResults[
	searchResults[, grep("aphyllous", colnames(searchResults))] == TRUE &
		rowSums(searchResults) > 1,
] <- FALSE

# consider logical relationships
searchResults[
	rowSums(searchResults[, grep("pinnate|palmate", colnames(searchResults))]) > 0,
	grep("compound", colnames(searchResults))
] <- TRUE


We can now write the data into the prepared new results matrix.

In [ ]:
# use the searchResults matrix to create new value strings by concatenating all data found
for (i in seq_along(searchResultsCols)) {
	searchResultsTemp <- searchResults[, colnames(searchResults) %in% searchResultsCols[[i]], drop = FALSE]
	newVals[, i] <- sapply(seq_len(nrow(searchResultsTemp)), function(x) {
		paste(searchResultsCols[[i]][searchResultsTemp[x, ]], collapse = ",")
	})
}
newVals[newVals == ""] <- NA


As some values belong to other traits, we move them there.

In [ ]:
# move values to other traits
TRY[TraitName == "Leaf compoundness", CleanedValueStr := newVals[, 2]]
TRY[TraitName == "Leaf compoundness", TraitName := "gotoLeaf shape"]


We can now inetegrate the new values into the TRY data.

In [ ]:
# integrate into TRY
TRY <- rbind(TRY, TRYSubset, fill = TRUE)
TRY[TraitName == "Leaf compoundness", CleanedValueStr := newVals[, 1]]


As we duplicated the data to accommodate the data belonging to other traits, to avoid an unnecessary increase
in file size, we remove the rows of the duplicated data without values in the "CleanedValueStr" column.

In [ ]:
TRY <- TRY[!grepl("^goto", TraitName) | !is.na(CleanedValueStr)]


We have used an existing trait name with the prefix "goto" to classify some data. This was done
to eventually move the data to the respective trait, but avoid another round of pre-processing.
So only run the following line if this is the last of various pre-processing scripts you want to use.

In [ ]:
TRY[, TraitName := sub("^goto", "", TraitName)]


Let's write the data to a file.

In [ ]:
fwrite(TRY, file = paste0("TRY_processed_", Sys.Date(), ".gz"))
